# Analyzing Neural Data Using Multiple Linear Regression
## Directional Tuning in Motor Cortex (Georgopoulos et al, 1982)
### Kass, Eden, and Brown, *Analysis of Neural Data*, Example 12.6

"In a well-known set of experiments, Georgopoulos, et al. showed that motor cortex neurons are directionally “tuned.” Figure 4 shows a set of raster plots for a “center-out” reaching task: the monkey reached to one of eight points on a circular image, and this neuron was much more active for reaches in some directions than for others. The bottom part of Fig. 4 shows a cosine function that has been fitted to the mean firing rate as a function of the angle around the circle, which indicates the direction of reach. For example (and as is also shown in the raster plots), reaches at angles near 180$^\circ$ from the  x-axis produced high firing rates, while those at angles close to 0$^\circ$ (movement to the right) produced much lower firing rates. The angle at which the maximum firing rate occurs is called the “preferred direction” of the cell. It is obtained from the cosine function.

To fit a cosine to a set of spike counts, multiple linear regression is used. Let  $v=(v_1,v_2)$ be the vector specifying the direction of movement and let  $d=(d_1,d_2)$ be the preferred direction for the neuron. Both  v and  d are unit vectors. Assuming cosine tuning, the firing depends only on  $\cos \theta$, where  $\theta$ is the angle between  v and  d. We have
\begin{aligned} \cos \theta = v\cdot d = v_1d_1+v_2d_2. \end{aligned}
Letting  $\mu (v)$ be the mean firing rate in a given interval of time when the movement is in direction  v, if we let the minimal firing rate be $B_{min}$ and the maximal firing rate be  $B_{max}$, then cosine tuning may be written as the requirement that
\begin{aligned} \mu (v) = B_{min} + \frac{B_{max}-B_{min}}{2} + \frac{B_{max}-B_{min}}{2}\cos \theta . \end{aligned}
(Recall that the minimal value of the cosine is  -1, and its maximal value is 1.) If we now define  $\beta _1 = \frac{B_{max}-B_{min}}{2}d_1,  \beta _2 = \frac{B_{max}-B_{min}}{2}d_2, and  \beta _0 = B_{min} + \frac{B_{max}-B_{min}}{2}$ we obtain the linear form:

\begin{aligned} \mu (v) = \beta _0 + \beta _1 v_1 + \beta _2 v_2. \end{aligned}

Taking  $C_i(v)$ to be the spike count for the  $i^{th}$ trial in direction  v across a time interval of length  T, the observed spike count per unit time is
\begin{aligned} Y_i(v) = \frac{1}{T}C_i(v). \end{aligned}

and we have

\begin{aligned} Y_i(v) = \mu (v) + \epsilon _i(v). \end{aligned}

Together, Eqs. (12.68) and (12.67) define a two-variable multiple linear regression model from which the tuning parameters may be obtained."

Figure 4, from Georgopoulos et al, 1982, JNeurosci:

![Georgopoulos et al., 1982, Figure 4](http://charlotte.neuro.brown.edu/~sheinb/courses/NEUR2060/images/georgopoulos82_figure4.png)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
np.random.seed(763342311)

### Visualizing *cos $\theta$*:

In [ ]:
%%html
<iframe  src="https://ggbm.at/q95c3mFG" width="800" height="500"> <\iframe>

### Generating spike trains to simulate the kind of data observed by Georgopoulos et al.
#### Copy code from our spikes and rasters homework

In [ ]:
def generate_spike_train(duration, rate):
    """
    Use probabilistic approach to generate spike trains
    :param duration: duration of train (in sec)
    :param rate: rate function
    :return: numpy array of spike times
    """
    dt = 1/1000.
    n = int(duration*1000)
    rands = np.random.uniform(0,1,n)
    times = np.flatnonzero(rands < rate*dt)
    return times*dt

def create_trials(n_trials, duration, rate):
    """
    generate n_trials spike trains with fixed rate
    :param n_trials: number of trials to simulate
    :param duration: length of trial in seconds
    :param rate: rates in spikes/sec
    :return: list of spike trains
    """
    return [generate_spike_train(duration, rate) for i in range(n_trials)]

def create_hist(spike_times, nbins, start, stop, n_trials):
    """
    compute histogram of spike times
    :param spike_times: flattened list of spike times (in sec)
    :param nbins: number of bins to use
    :param start: start time for histogram window
    :param stop: stop time for histogram window
    :param n_trials: number of trials in this spike list
    :return: (list of starting position of bars, rates for each bar)
    """
    duration = float(stop)-start
    counts, xs = np.histogram(spike_times, nbins, range=(start, stop))
    rates = (counts / n_trials) / (duration / nbins)
    binwidth = xs[1]-xs[0]
    return xs[:-1]+(binwidth/2.), rates

def create_response_function(duration, onset_time, spontaneous, peak, final_rate):
    """
    return simulated neural response, with onset latency and exponential falloff
    :param duration: length (in sec) of function
    :param onset_time: time at which stimulus response begins (in sec)
    :param spontaneous: spontaneous rate before stimulus response
    :param peak: peak rate at onset_time
    :param final_rate: rate that the function falls to by end of duration period
    :return: array of values sampled at ms resolution mimicking neural response
    """
    n = int(duration*1000)
    # Make pretime a fixed value until onset_time
    pretime = int(1000*onset_time)
    
    # Posttime corresponds to the number of ms in the total where the actual response is
    posttime = int(n-pretime)
    
    # Here's the fixed background rate
    background = np.repeat(spontaneous,pretime)
    
    # These steps help us define an exponential fallout that falls from peak to final_rate
    proportion = final_rate/peak
    end = -np.log(proportion)
    
    # Having setup up the 
    resp = peak*np.e**(-np.linspace(0,end,posttime))
    return np.concatenate((background,resp))

### Generate spike trains using the *response function*

Here we follow the notation described above in the Kass et al. formulation of this experiment.  The basic idea is that the most effective movement (the preferred movement direction) will generate the greatest response (B_max).  The null direction, 180 degrees away from the preferred direction, will yield a response of B_min.

In [ ]:
def create_spike_trains(duration, onset, n_trials_per_cond, B_min, B_max):
    # halfway between min and max, around which sinusoidal modulation occurs
    midpoint = (B_max-B_min)/2
    angles = np.linspace(-135,180,8)

    # here we generate target rates for each angle
    rates = B_min+midpoint+midpoint*np.cos(np.deg2rad(angles))

    all_trains = []
    all_angles = np.repeat(angles, n_trials_per_cond)

    for rate in rates:
        rate_function = create_response_function(duration, .1, 10, rate, 10)
        trains = create_trials(n_trials_per_cond, duration, rate_function)
        all_trains += trains

    return all_angles, all_trains

### Now create trains and store conditions and spike times

* For each angle, create 20 one sec spike trains with response onset at 100ms
* Miniumum rate is 5Hz, maximum 110Hz

In [ ]:
all_angles, all_trains = create_spike_trains(1.0, 0.1, 20, 5, 110)

#### Check the current angles in our data

In [ ]:
np.unique(all_angles)

#### And use our raster code to look at the data

In [ ]:
from rasters import plot_rasters
plot_rasters(all_angles, all_trains, max_rate=120)

#### Now we want a function to turn our spike trains into rates

In [ ]:
def spike_rates(trains, start, stop):
    '''count number of spikes for each train between start, stop (sec) and convert to rates'''
    duration = stop-start
    rates = [np.sum(np.logical_and(train >= start, train < stop)/duration)
              for train in trains]
    return rates

#### Get rates for various epochs ([0ms,100ms], [100ms,300ms], [500ms,800ms])

We want to explore the rates for a few windows which we'll combine into a single dataset below.  Here get rates for the desire epochs (remember that our functions takes seconds).

In [ ]:
spike_rates_0_100 = spike_rates(****, ****, ****)
spike_rates_100_300 = spike_rates(****, ****, ****)
spike_rates_500_800 = spike_rates(****, ****, ****)

In [ ]:
spike_rates_100_300[0:10]

## Using pandas to manage our data

#### Start by creating a new dataframe with the independent variable (angles) and three different dependent variables

In [ ]:
import pandas as pd

df = pd.DataFrame({"angle": all_angles, 
                   "rate_0_100": ****, 
                   "rate_100_300": ****,
                   "rate_500_800": ****})

Take a quick look at the `head()` of the DataFrame to make sure it looks good:

In [ ]:
df.head()

Now use the `groupby()` function to sort our trials by angle and take the means of the grouped data:

In [ ]:
df.groupby(****).****

To visualize these data, chain the plot function after taking the means as `.plot(kind=bar)`:

In [ ]:
_ = ****.plot(kind='bar')

To show individual rates, you can use the `.plot.scatter()` function specifying the `x=` and `y=` arguments.  Try to make a scatter of the rates between 100ms and 300ms as a function of angle:

In [ ]:
_ = df.plot.scatter(****, ****)

Now make the scatter for the rates between 500ms and 800ms as a function of angle.

In [ ]:
_ = df.plot.scatter(****, ****)

### The multiple regression

Here we add two *derived* columns to our dataframe corresponding to the cartesian x and y movements (in the range -1 to 1).  These are simply the cosine and sine of the `angle` column (after converting to radians).

In [ ]:
df['movement_x'] = np.cos(np.deg2rad(df['angle']))
df['movement_y'] = np.sin(np.deg2rad(df['angle']))

And finally we come to the multiple regression step.  We'll use the statsmodels `sm.ols()` function, which takes a `formula=` parameter specifying our model and the name of our data frame as `data=`.  We can chain a `fit()` function to this `sms.ols()` object."

In [ ]:
import statsmodels.formula.api as sm
result = sm.ols(formula="rate_100_300 ~ movement_x + movement_y", data = df).fit()

In [ ]:
print(result.params)

In [ ]:
print(result.summary())

#### Using the model to make predictions

After fitting the model we can predict y values for both x values in the dataset and new x values.  We'll start with the unique angles we initially fed into the model:

In [ ]:
pred_df = pd.DataFrame({"movement_x" : np.cos(np.deg2rad(np.unique(all_angles))), 
                        "movement_y" : np.sin(np.deg2rad(np.unique(all_angles)))})
result.predict(pred_df)

We can compare these predictions to the actual 100ms-300ms rates for each condition:

In [ ]:
df.groupby('angle').mean()

Now try to fit the model to 100 points evenly spaced between -180 and 180 degrees:

In [ ]:
newangles = ****
pred_df = pd.DataFrame({"angles" : ****,
                        "movement_x" : ****, 
                        "movement_y" : ****})
predictions = result.predict(pred_df)

Now make a scatter plot of the actual rate_100_300 values (`df['rate_100_300']`) vs angle (`df['angle]`), and then overlay the `predictions` as a function of `newangles`:

In [ ]:
plt.plot(****, ****,'o')
_ = plt.plot(****, ****)

### Exporting data for analysis or exploration in another program

Use **pandas.to_XXX*** for your target format.

E.g.:

```python
df.to_csv('motortuning.csv')
df.to_excel('motortuning.xls')
```

In [ ]:
df.to_csv('motortuning.csv')
df.to_excel('motortuning.xls')

#### In R

``` R
df = read.csv('motortuning.csv')
results = lm(formula = rates_100_300 ~ movement_x + movement_y, data = df)
summary(results)


Call:
lm(formula = rates_100_300 ~ movement_x + movement_y, data = df)

Residuals:
    Min      1Q  Median      3Q     Max 
-35.908 -10.094  -1.054   8.221  50.177 

Coefficients:
            Estimate Std. Error t value Pr(>|t|)    
(Intercept)   46.344      1.202  38.557   <2e-16 ***
movement_x    40.290      1.700  23.702   <2e-16 ***
movement_y     1.521      1.700   0.895    0.372    
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

Residual standard error: 15.2 on 157 degrees of freedom
Multiple R-squared:  0.7818,	Adjusted R-squared:  0.779 
F-statistic: 281.3 on 2 and 157 DF,  p-value: < 2.2e-16


```

And the ANOVA table:

```R
summary(aov(results))

             Df Sum Sq Mean Sq F value Pr(>F)    
movement_x    1 129860  129860 561.791 <2e-16 ***
movement_y    1    185     185   0.801  0.372    
Residuals   157  36291     231                   
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1
```